hour=9,
minute=3 (더 정확하게는 minute <= 4)

입력 시 make_rhists에서 에러가 나고 있음.
이때의 에러는, 특정 교차로에 대하여 history 데이터가 없기 때문으로 추정됨.

특정 교차로에 대하여 history가 없더라도 에러가 나지 않도록 디버깅하려고 시도했으나, 일단 잘 되지 않았음. 나중으로 미룸 (2024. 8. 2. 09:27)

In [1]:
import pandas as pd
import numpy as np
import os, sys, json, argparse, pickle
import sumolib, traci
from tqdm import tqdm
from datetime import datetime
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
path_scr = os.path.join(path_root, 'scripts')
sys.path.append(path_scr)
from generate_signals import SignalGenerator

In [2]:
self = SignalGenerator(config_name='test_0731',
                       month=7,
                       day=31,
                       hour=9,
                       minute=3)
self.prepare_data()
self.make_rhistory()
# display(self.rhistory.head())
# self.make_rhists()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-5. 필요한 보조 객체들이 모두 준비되었습니다.


In [3]:
print(self.inter_nos)
inter_no = 457

[436, 437, 438, 442, 443, 455, 456, 457, 458]


In [6]:
print(self.present_time)
self.history[self.history.inter_no==457]

1722384000


end_unix  inter_no  dura_A1  dura_A2  dura_A3  dura_A4  dura_A5  \
5   1722384411       457       45       20       40       40       35   
11  1722384773       457       45       20       40       40       35   
26  1722384591       457       45       20       40       40       35   
33  1722384053       457       45       20       40       35       40   
36  1722384232       457       45       20       40       40       35   
43  1722384953       457       45       20       40       40       35   

    dura_A6  dura_A7  dura_A8  dura_B1  dura_B2  dura_B3  dura_B4  dura_B5  \
5         0        0        0       45       20       40       40       35   
11        0        0        0       45       20       40       40       35   
26        0        0        0       45       20       40       40       35   
33        0        0        0       45       20       40       35       40   
36        0        0        0       45       20       40       40       35   
43        0        0        0       45       20       40       40       35   

    dura_B6  dura_B7  dura_B8  
5         0        0        0  
11        0        0        0  
26        0        0        0  
33        0        0        0  
36        0        0        0  
43        0        0        0

In [4]:
self.rhistory[self.rhistory.inter_no==457]

inter_no  start_unix  dura_A1  dura_A2  dura_A3  dura_A4  dura_A5  dura_A6  \
0       457  1722384400       45       20       40       35       40        0   
0       457  1722384400       45       20       40       35       40        0   
0       457  1722384400       45       20       40       40       35        0   

   dura_A7  dura_A8  dura_B1  dura_B2  dura_B3  dura_B4  dura_B5  dura_B6  \
0        0        0       45       20       40       35       40        0   
0        0        0       45       20       40       35       40        0   
0        0        0       45       20       40       40       35        0   

   dura_B7  dura_B8  cycle  
0        0        0  180.0  
0        0        0  180.0  
0        0        0  180.0

In [ ]:
self.make_rhists()

In [ ]:
rhistory = self.history[self.history.inter_no==inter_no]
rhistory = rhistory[(rhistory.end_unix <= self.present_time) & (rhistory.end_unix > self.present_time - self.subtractor)]
rhistory

In [ ]:
# rhistory에 모든 교차로번호가 존재하지 않으면 해당 교차로번호에 대한 신호이력을 추가함 (at 최근 프로그램 시작시각)
inter_no = inter_no
program_start, prow = self.load_prow(inter_no, self.present_time - self.subtractor)
cycle = prow.cycle.iloc[0]
row1 = prow.copy()
row2 = prow.copy()
# prow에서 필요한 부분을 rhistory에 추가
row1['end_unix'] = program_start
row2['end_unix'] = program_start + cycle
display(row1)
display(row2)
rhistory = pd.concat([rhistory, row1, row2])#.reset_index(drop=True)
rhistory

In [ ]:
# present_time + adder 의 시각에 한 주기의 신호 추가
program_start, prow = self.load_prow(inter_no, self.present_time)
cycle = prow.cycle.iloc[0]
row3 = prow.copy()
# # prow에서 필요한 부분을 rhistory에 추가
row3['end_unix'] = self.present_time + self.adder
rhistory = pd.concat([rhistory, row3])#.reset_index(drop=True)
rhistory

In [ ]:
display(rhistory)
i = 0
row = rhistory.iloc[i]
inter_no = row.inter_no
end_unix = row.end_unix
elapsed_time = row[[f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)]].sum() // 2 # 현시시간 합
# 이전 유닉스 존재하지 않음 : 현시시간 합의 차
start_unix = end_unix - elapsed_time
pre_rows = self.history[:i] # previous rows
print(inter_no in pre_rows.inter_no.unique())
if inter_no in pre_rows.inter_no.unique(): # 이전 유닉스 존재
    pre_unix = pre_rows[pre_rows.inter_no == inter_no]['end_unix'].iloc[-1] # previous unix time
    # 이전 유닉스 존재, abs < 10 : 이전 유닉스
    if abs(pre_unix - start_unix) < 10:
        start_unix = pre_unix
    # 이전 유닉스 존재, abs >=10 : 현시시간 합의 차
    else:
        pass
rhistory.loc[i, 'start_unix'] = start_unix
rhistory


In [ ]:
self.inter_nos